## Compare the results of 2 global discharge models with in situ information

Notebook prepared by Ben Maathuis, Willem Nieuwenhuis and Bas Retsios. ITC-University of Twente, Enschede. The Netherlands

Through this notebook you will retrieve and process data from GEOGLOWS and GLoFAS and compare the model results on daily discharge also with in situ information of a gauging station. The Rhine river, entering the Netherlands, at the town of Lobith is taken as the common location for which both model and insitu data is available.

Download the sample data (the in situ discharge information from 1990 to mid-2025). When execuing the notebook, the sample data is expected in a folder in the notebook directory and the folder name expected is 'Qmodel_insitu' and is containing a single csv file named:'Q_Lobith_1990_2025_insitu.csv'.

You will use observations which are linked to a stream segment (in case of GEOGLOWS), observations derived from yearly temporal aggregated GRIB files (in the case of GLoFAS) in conjunction with data derived from a SCV file (in situ observations). Once the data is retieved using various libraries, all data is furhter processed in Pandas and visual comparisons are made in Matplotlib.

Links for review of the model / data sources are provided below.

#### For GEOGLOWS
See for further information:
+ geoglows website ECMWF: https://geoglows.ecmwf.int/ - webapp: https://hydroviewer.geoglows.org/
+ geoglows model: https://geoglows.readthedocs.io/en/latest/
+ geoglows use in notebook:  https://colab.research.google.com/drive/19PiUTU2noCvNGr6r-1i9cv0YMduTxATs?usp=sharing#scrollTo=CGU2lke5miuR

#### For GLoFAS
See for further information:
+ the GloFAS system: https://www.globalfloods.eu/
+ the data will be retrieved in grib2 format, for further information on data download see: https://ewds.climate.copernicus.eu/datasets/cems-glofas-historical?tab=download

#### For In Situ
See for further information:
+ online discharge info the netherlands: https://waterdata.wrij.nl/index.php?wat=kaart-esri
+ online discharge used: https://waterdata.wrij.nl/index.php?wat=download&deeplink=0&lokid=36393&tsid=16979042
+ note: the in situ data of the Lobith gauging station - mean daily discharge in m3/sec - has already been retrieved and is provided as sample data (in the file 'Q_Lobith_1990_2025_insitu.csv')

### Process GEOGLOWS

You can Install the GEOGLOWS API client via the package management system pip, type the following command promt window in the python folder: !pip install geoglows - see the first line in the code field below, uncomment the line if the GEOGLOWS package is not installed.

Now you are ready to start retrieving data from GEOGLOWS.

#### Select the segment of streamnetwork to get the 'StreamID' code:
+ https://geoglows.ecmwf.int/
+ StreamID = 230546613 (used here: representing the location of the Rhine river entering the Netherlands - at the in situ station Lobith)

In [ ]:
#uncomment the line below to install the geoglows package if not done before
#!pip install geoglows

In [ ]:
import os
from osgeo import gdal, osr
import ilwis
import geoglows
import numpy as np
import pandas as pd
from datetime import date
from datetime import datetime, timedelta
import matplotlib.pyplot as plt
import matplotlib.dates as mdates
import warnings
warnings.filterwarnings('ignore')

In [ ]:
#set sample data folder
#use the Python function os.getcwd() to retrieve the current folder used and add the apporriate sub-folder
work_dir = os.getcwd() + r'/Qmodel_insitu'

#set the working directory for ILWISPy
ilwis.setWorkingCatalog(work_dir)
print(ilwis.version())
print(work_dir)

#### For Historical Simulation:

geoglows.data.retrospective(*args, **kwargs)

+ Retrieves the retrospective simulation of streamflow for a given river_id from s3 buckets

Parameters:
+ river_id (int) – the ID of a stream, should be a 9 digit integer

Keyword Arguments:
+ format (str) – the format to return the data, either ‘df’ or ‘xarray’. default is ‘df’

+ storage_options (dict) – options to pass to the xarray open_dataset function

+ resolution (str) – resolution of data to retrieve: hourly, daily, monthly, or yearly. default hourly

Returns:
+ pd.DataFrame or xr.Dataset

In [ ]:
StreamID = 230546613 #Rhine river entering the Netherlands, near Lobith

In [ ]:
df_geoglows = geoglows.data.retrospective(StreamID, resolution = 'daily')

In [ ]:
df_geoglows

In [ ]:
#using the hydroviewer of geoglows providing some interactive functionality
hydroviewer_figure = geoglows.plots.retrospective(df_geoglows)
hydroviewer_figure.show()

We continue working with Pandas

In [ ]:
#check the dataframe
df_geoglows.head

In [ ]:
#Reset index first to bring 'time' back into a column
df_geoglows = df_geoglows.reset_index()

#Rename columns
df_geoglows = df_geoglows.rename(columns={ (StreamID): 'discharge'})

In [ ]:
df_geoglows

In [ ]:
# Selecting a certain time range
mask = (df_geoglows['time'] >= '2022-01-01') & (df_geoglows['time'] <= '2024-12-31')
df_geoglows_sel = df_geoglows.loc[mask]

In [ ]:
#create the plot
plt.figure(figsize =(12, 6))
plt.plot(df_geoglows_sel['time'], df_geoglows_sel['discharge'],label='Q-Lobith - GEOGLOWS')
plt.xlabel('Date')
plt.ylabel('Discharge (m³/s)')
plt.title('GEOGLOWS model discharge Rhine, Lobith - The Netherlands')
#plt.xticks(rotation=45)
plt.legend()
plt.grid()
plt.tight_layout()
plt.show();

In [ ]:
#save file
df_geoglows.to_csv(work_dir+'/GEOGLOWS_Lobith.csv')
df_geoglows_sel.to_csv(work_dir+'/GEOGLOWS_Lobith_2022_2024.csv')

### Process GLoFAS

### Retrieve the data from the Copernicus CEMS Early Warning Data Store
See also: https://ewds.climate.copernicus.eu/how-to-api

Login to the climate data store, register and if you click on the name you get the details of your user profile. Copy and paste the personal access token to a text file and change it according to the two line example below:

        url: https://ewds.climate.copernicus.eu/api
        key: <PERSONAL-ACCESS-TOKEN>

Save this text file at the follwoing location and filename: C:\Users\<USERNAME>\.cdsapirc

#### Install and import the cdsapi 
Install the cdsapi: The CDS API client is a python based library. It provides support for Python 3.

You can Install the CDS API client via the package management system pip, type the following command promt window in the python folder: 

+ !pip install cdsapi - see code field below

Now you are ready to start retrieving data from the CDS

Link to data portal: https://ewds.climate.copernicus.eu/datasets/cems-glofas-historical?tab=download

Limitation of data download is that only up to 500 layers (days) can be retrieved given a download request, so here a yearly data download of the area of interest is used. From the link above generate  a data request and review the resulting api request and compare it with the code fields below.

In [ ]:
#Uncomment the line below to install the cdsapi if not already done before
#!pip install cdsapi

In [ ]:
import cdsapi

In [ ]:
year = '2022'
dataset = "cems-glofas-historical"
request = {
    "system_version": ["version_4_0"],
    "hydrological_model": ["lisflood"],
    "product_type": ["consolidated"],
    "variable": ["river_discharge_in_the_last_24_hours"],
    "hyear": [ year ],
    "hmonth": [
        "01","02","03","04","05","06","07","08","09","10","11","12"
    ],
    "hday": [
        "01","02","03","04","05","06","07","08","09","10",
        "11","12","13","14","15","16","17","18","19","20",
        "21","22","23","24","25","26","27","28","29","30","31"
    ],
    "data_format": "grib2",
    "download_format": "unarchived",
    "area": [51.75, 5.95, 51.95, 6.12] # North, West, South, East - Lobith
}
client = cdsapi.Client()
client.retrieve(dataset, request, (work_dir) +'/' +'historical_' + year + '_lobith.grib')

In [ ]:
year = '2023'
dataset = "cems-glofas-historical"
request = {
    "system_version": ["version_4_0"],
    "hydrological_model": ["lisflood"],
    "product_type": ["consolidated"],
    "variable": ["river_discharge_in_the_last_24_hours"],
    "hyear": [ year ],
    "hmonth": [
        "01","02","03","04","05","06","07","08","09","10","11","12"
    ],
    "hday": [
        "01","02","03","04","05","06","07","08","09","10",
        "11","12","13","14","15","16","17","18","19","20",
        "21","22","23","24","25","26","27","28","29","30","31"
    ],
    "data_format": "grib2",
    "download_format": "unarchived",
    "area": [51.75, 5.95, 51.95, 6.12] # North, West, South, East - Lobith
}
client = cdsapi.Client()
client.retrieve(dataset, request, (work_dir) +'/' +'historical_' + year + '_lobith.grib')

In [ ]:
year = '2024'
dataset = "cems-glofas-historical"
request = {
    "system_version": ["version_4_0"],
    "hydrological_model": ["lisflood"],
    "product_type": ["consolidated"],
    "variable": ["river_discharge_in_the_last_24_hours"],
    "hyear": [ year ],
    "hmonth": [
        "01","02","03","04","05","06","07","08","09","10","11","12"
    ],
    "hday": [
        "01","02","03","04","05","06","07","08","09","10",
        "11","12","13","14","15","16","17","18","19","20",
        "21","22","23","24","25","26","27","28","29","30","31"
    ],
    "data_format": "grib2",
    "download_format": "unarchived",
    "area": [51.75, 5.95, 51.95, 6.12] # North, West, South, East - Lobith
}
client = cdsapi.Client()
client.retrieve(dataset, request, (work_dir) +'/' +'historical_' + year + '_lobith.grib')

#### Check location of river to retrieve discharge values from
Quick review of the data retrieved, including the meta data

In [ ]:
#select and load the dataset
grib_content = work_dir +'/'+'historical_2022_lobith.grib'
glofas_2022 = ilwis.RasterCoverage(grib_content)
print(glofas_2022.size())

#retrieve the first layer of the dataset
area_retrieved = ilwis.do('selection',glofas_2022,"rasterbands(0)")
print(area_retrieved.size())

In [ ]:
#convert ilwis array to numpy array
area_retrieved_2np = np.fromiter(iter(area_retrieved), np.float64, area_retrieved.size().linearSize()) 
area_retrieved_2np = area_retrieved_2np.reshape((area_retrieved.size().ysize, area_retrieved.size().xsize))

# Plot the 2D array using matplotlib
plt.imshow(area_retrieved_2np, cmap='jet')
plt.title('First Layer of Raster Stack')
plt.colorbar(label='Pixel values')
plt.axis('off')
plt.show()

#### Checking the meta data  - using the REF_TIME
Each layer has a (GRIB) reference time, execute the field below to check the order of the REF-TIME. What can you conclude? Note the operation performed is using gdal.info

In [ ]:
dataset = gdal.Open(grib_content)
for i in range(1, min(dataset.RasterCount, 60) + 1):  # Only check first 60 bands
    band = dataset.GetRasterBand(i)
    metadata = band.GetMetadata()
    print(f"Band {i} GRIB_IDS:\n{metadata.get('GRIB_IDS', 'N/A')}\n")

Extract the UNIX timestamps and convert these into readable datetime strings

In [ ]:
#extract the unix-time (seconds since Jan 01 1970. (UTC))
ref_times = []

print("Band | GRIB_REF_TIME")
print("-" * 30)

for i in range(1, dataset.RasterCount + 1):
    band = dataset.GetRasterBand(i)
    metadata = band.GetMetadata()
    ref_time = metadata.get('GRIB_REF_TIME')
    ref_times.append(ref_time)
    print(f"{i:4} | {ref_time}")

In [ ]:
# Convert and print human-readable dates
print("Band | GRIB_REF_TIME (UTC)")
print("-" * 35)

for i, ref_time in enumerate(ref_times, start=1):
    if ref_time:
        dt = datetime.utcfromtimestamp(int(ref_time.split()[0])).isoformat() + 'Z'
    else:
        dt = "N/A"
    print(f"{i:4} | {dt}")

#### Process Historical 2022 - 2024 data using GDAL
Note from the inventory above that first the month of February is presented, then the months having 30 days and finaly the months having 31 days!
To import the data layers in the grib file we will use the reference time to ensure the appropriate temporal ordering!

In [ ]:
# read and process the 2024 GRIB raster data
#eventually uncomment the 'print' commands to see the output
historical_grib_file_2024 = work_dir +'/'+'historical_2024_lobith.grib'
glofas_historical_2024 = ilwis.RasterCoverage(historical_grib_file_2024)
dataset = gdal.Open(historical_grib_file_2024)

#create a 3d stack stack using the 'grib reference time' to order the grib layers
date_historical = []
for i in range(1, dataset.RasterCount + 1):
    date = dataset.GetRasterBand(i).GetMetadata()['GRIB_REF_TIME']
    date = date.split()[0]
    date_historical.append(date)
date_historical = [datetime.fromtimestamp(int(date)) for date in date_historical]
#date_historical

l = 1
c = 2 
z = (glofas_historical_2024.size().zsize)
#print(z)

Q_2024 = []
for n in range(0,(z)):
    point_value = (glofas_historical_2024.pix2value(ilwis.Pixel(c,l,n)))
    Q_2024.append(point_value)

#print('Values extracted for selected location:', Q_2024)

data = sorted(zip(date_historical, Q_2024))
df2024= pd.DataFrame(data, columns=['date', 'discharge'])
date_historical = np.array(df2024.date)
Q_2024 = np.array(df2024.discharge)
#print(date_historical)

fig = plt.figure(figsize =(14, 7))
plt.plot(date_historical, Q_2024, label='Discharge')
plt.xlabel('Time')
plt.ylabel('Discharge (m3/sec)')
plt.title('Discharge Rhine  - at Lobith (the Netherlands)')
plt.legend()

In [ ]:
# read and process the 2023 GRIB raster data
#eventually uncomment the 'print' commands to see the output
historical_grib_file_2023 = work_dir +'/'+'historical_2023_lobith.grib'
glofas_historical_2023 = ilwis.RasterCoverage(historical_grib_file_2023)
dataset = gdal.Open(historical_grib_file_2023)

#create a 3d stack stack using the 'grib reference time' to order the grib layers
date_historical = []
for i in range(1, dataset.RasterCount + 1):
    date = dataset.GetRasterBand(i).GetMetadata()['GRIB_REF_TIME']
    date = date.split()[0]
    date_historical.append(date)
date_historical = [datetime.fromtimestamp(int(date)) for date in date_historical]
#date_historical

l = 1
c = 2 
z = (glofas_historical_2023.size().zsize)
#print(z)

Q_2023 = []
for n in range(0,(z)):
    point_value = (glofas_historical_2023.pix2value(ilwis.Pixel(c,l,n)))
    Q_2023.append(point_value)

#print('Values extracted for selected location:', Q_2023)

data = sorted(zip(date_historical, Q_2023))
df2023= pd.DataFrame(data, columns=['date', 'discharge'])
date_historical = np.array(df2023.date)
Q_2023 = np.array(df2023.discharge)
#print(date_historical)

fig = plt.figure(figsize =(14, 7))
plt.plot(date_historical, Q_2023, label='Discharge')
plt.xlabel('Time')
plt.ylabel('Discharge (m3/sec)')
plt.title('Discharge Rhine  - at Lobith (the Netherlands)')
plt.legend()

In [ ]:
# read and process the 2022 GRIB raster data
#eventually uncomment the 'print' commands to see the output
historical_grib_file_2022 = work_dir +'/'+'historical_2022_lobith.grib'
glofas_historical_2022 = ilwis.RasterCoverage(historical_grib_file_2022)
dataset = gdal.Open(historical_grib_file_2022)

#create a 3d stack stack using the 'grib reference time' to order the grib layers
date_historical = []
for i in range(1, dataset.RasterCount + 1):
    date = dataset.GetRasterBand(i).GetMetadata()['GRIB_REF_TIME']
    date = date.split()[0]
    date_historical.append(date)
date_historical = [datetime.fromtimestamp(int(date)) for date in date_historical]
#date_historical

l = 1
c = 2 
z = (glofas_historical_2022.size().zsize)
#print(z)

Q_2022 = []
for n in range(0,(z)):
    point_value = (glofas_historical_2022.pix2value(ilwis.Pixel(c,l,n)))
    Q_2022.append(point_value)

#print('Values extracted for selected location:', Q_2022)

data = sorted(zip(date_historical, Q_2022))
df2022= pd.DataFrame(data, columns=['date', 'discharge'])
date_historical = np.array(df2022.date)
Q_2022 = np.array(df2022.discharge)
#print(date_historical)

fig = plt.figure(figsize =(14, 7))
plt.plot(date_historical, Q_2022, label='Discharge')
plt.xlabel('Time')
plt.ylabel('Discharge (m3/sec)')
plt.title('Discharge Rhine  - at Lobith (the Netherlands)')
plt.legend();

#### Plot all year / series together

In [ ]:
GLoFAS_all = pd.concat([df2022, df2023, df2024], ignore_index=True)
print(len(GLoFAS_all))

In [ ]:
fig = plt.figure(figsize =(12, 6))
plt.plot(GLoFAS_all['date'], GLoFAS_all['discharge'])
plt.xlabel('Date')
plt.ylabel('Discharge (m³/s)')
plt.title('GLoFAS model discharge Rhine, Lobith - The Netherlands')
#plt.xticks(rotation=45)
plt.legend()
plt.grid()
plt.tight_layout()
plt.show();

In [ ]:
#save file
GLoFAS_all.to_csv(work_dir+'/Glofas_Lobith_2022_2024.csv')
GLoFAS_all

### Processing the In Situ Daily Mean Discharge

In [ ]:
# data source: WaterInformatie @ Waterschap Rijn en IJssel - https://waterdata.wrij.nl/
# file available in your sample data folder
#inspect the file using e.g. notepad and check the content
file = work_dir+'/Q_Lobith_1990_2025_insitu.csv'

In [ ]:
# Load the CSV file
df_gauge = pd.read_csv(
    file,                         # note name above
    sep=",",                      # Semicolon as delimiter
    parse_dates=["Date"]          # Parse datetime column
)

In [ ]:
#perform some additonal data fram modifications
start_date = pd.to_datetime('1990-01-01')
df_gauge['date_new'] = start_date + pd.to_timedelta(df_gauge.index, unit='D')
df_gauge['discharge_m3s'] = df_gauge['Discharge'] / 1000

In [ ]:
#check the dataframe content
df_gauge

In [ ]:
# Selecting a certain time range
mask = (df_gauge['date_new'] >= '2022-01-01') & (df_gauge['date_new'] <= '2024-12-31')
df_gauge_sel = df_gauge.loc[mask]

In [ ]:
# Plot using matplotlib
plt.figure(figsize=(12, 6))
plt.plot(df_gauge_sel["date_new"], df_gauge_sel["discharge_m3s"], label="Q-Lobith - In Situ")
plt.xlabel("Date")
plt.ylabel("Discharge (m³/s)")
plt.title("In Situ discharge measurements Rhine, Lobith - The Netherlands")
#plt.xticks(rotation=45)
plt.legend()
plt.grid()
plt.tight_layout()
plt.show();

#### Plot of the 3 discharge time series for the years 2022, 2023 and 2024

In [ ]:
# Plot using matplotlib
plt.figure(figsize=(12, 6))
plt.plot(df_gauge_sel["date_new"], df_gauge_sel["discharge_m3s"], label='Q-Lobith - In-situ')
plt.plot(df_geoglows_sel['time'], df_geoglows_sel['discharge'],label='Q-Lobith - GEOGLOWS')
plt.plot(GLoFAS_all['date'], GLoFAS_all['discharge'],label='Q-Lobith - GLoFAS')
plt.xlabel("Date")
plt.ylabel("Discharge (m³/s)")
plt.title("Discharge comparison global discharge model output versus in situ observation for the Rhine river at Lobith, the Netherlands")
plt.grid(True)
plt.legend()
plt.tight_layout()
plt.show()

What can visually be observed when inspecting the figure above?

#### Some statistics
Create a new dataframe with the discharge values for insitu, geoglows and glofas 

In [ ]:
df1 = df_gauge_sel.reset_index(drop=True)
df2 = df_geoglows_sel.reset_index(drop=True)
df3 = GLoFAS_all.reset_index(drop=True)

In [ ]:
new_df = pd.DataFrame({'insitu': df1['discharge_m3s'],'geoglows': df2['discharge'],'glofas': df3['discharge']})

In [ ]:
new_df

In [ ]:
# get correlation coefficients
corr_insitu_geoglows = new_df['insitu'].corr(new_df['geoglows'])
corr_insitu_glofas = new_df['insitu'].corr(new_df['glofas'])

# Print results
print("Correlation (insitu & geoglows):", corr_insitu_geoglows)
print("Correlation (insitu & glofas):", corr_insitu_glofas)

### Compare the in situ observations and the GEOGLOW model output
For GLoFAS only 3 years for data is being processed in this notebook, but for the in situ and GEOGLOWs there is a longer common time period. Now let's inspect about 25 years of daily discharge data

In [ ]:
# Selecting a certain time range
mask = (df_geoglows['time'] >= '1990-01-01') & (df_geoglows['time'] <= '2024-12-31')
df_geoglows_sel1 = df_geoglows.loc[mask]

mask = (df_gauge['date_new'] >= '1990-01-01') & (df_gauge['date_new'] <= '2024-12-31')
df_gauge_sel1 = df_gauge.loc[mask]

In [ ]:
# Plot using matplotlib
plt.figure(figsize=(12, 6))
plt.plot(df_gauge_sel1["date_new"], df_gauge_sel1["discharge_m3s"], label='Q-Lobith - In-situ')
plt.plot(df_geoglows_sel1['time'], df_geoglows_sel1['discharge'],label='Q-Lobith - GEOGLOWS')
plt.xlabel("Date")
plt.ylabel("Discharge (m³/s)")
plt.title("Discharge comparison global discharge model output versus in situ observation for the Rhine river at Lobith, the Netherlands ")
plt.grid(True)
plt.legend()
plt.tight_layout()
plt.show();

#### Correlation coefficient over some longer time range for insitu and geoglows discharge comparison
As we compared only a shorter time series of GEOGLOWS against the in situ measurements above, we can also check if for a longer time period the correlation is changing as we have the common data series from 1990 onwards 

In [ ]:
# Selecting a longer common time range from the insitu dataframe
mask = (df_gauge['date_new'] >= '1990-01-01') & (df_gauge['date_new'] <= '2024-12-31')
df_gauge_sel2 = df_gauge.loc[mask]

# Selecting a longer common time range from the geoglows dataframe
mask = (df_geoglows['time'] >= '1990-01-01') & (df_geoglows['time'] <= '2024-12-31')
df_geoglows_sel2 = df_geoglows.loc[mask]

In [ ]:
df1_long = df_gauge_sel2.reset_index(drop=True)
df2_long = df_geoglows_sel2.reset_index(drop=True)

In [ ]:
new_df_long = pd.DataFrame({'insitu': df1_long['discharge_m3s'],'geoglows': df2_long['discharge']})

In [ ]:
new_df_long

In [ ]:
# get correlation coefficients
corr_insitu_geoglows_long = new_df_long['insitu'].corr(new_df_long['geoglows'])

# Print results
print("Correlation (insitu & geoglows):", corr_insitu_geoglows_long)

### Eventually select another time range of GLoFAS and conduct another temporal comparison yourself